This notebook can be executed on either cpu or gpu runtime.

To run on gpu, change the
```
.to('cpu')
```
to

```
.to('gpu')
```

In [ ]:
# Download nessecary libraries
!pip install datasets==2.10.0 --quiet
!pip install transformers --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 12.8 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive/')
root_dir = "./drive/MyDrive/ASR_Colab/" #change it to your own path

Mounted at /content/drive/


In [ ]:
# Load the preprocessed dataet
from datasets import load_from_disk
from os import path
import numpy as np

ds_test = load_from_disk(path.join(root_dir , "dataset.hf/test"))

In [ ]:
from transformers import  Wav2Vec2CTCTokenizer ,Wav2Vec2FeatureExtractor,Wav2Vec2Processor

tokenizer = Wav2Vec2CTCTokenizer(path.join(root_dir ,"vocab.json"), unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [ ]:
# Load the model weights
from transformers import Wav2Vec2ForCTC
model = Wav2Vec2ForCTC.from_pretrained(path.join(root_dir ,"model_weights")).to("cpu")

In [ ]:
# select 20 random samples from the test dataset
selected_samples = np.random.randint(low = 0 , high= len(ds_test) , size=20)

In [ ]:
import torch

# Initialize empty lists to store predicted outputs and other columns
predicted = []
real_sentences = []
audios = []
gender = []
accent = []
tone = []


# Iterate through the selected samples in the test dataset
for sample in ds_test.select(selected_samples):
  model_input = processor(sample["input_values"], return_tensors="pt", padding=True,sampling_rate=16000)

  # Move the input values to GPU and obtain model predictions
  logits = model(model_input.input_values.to("cpu")).logits
  pred_ids = torch.argmax(logits, dim=-1)[0]

  # Append the predicted output, real sentence labels, and audio inputs and other columns to their respective lists
  predicted.append(pred_ids)
  real_sentences.append(sample["transcript"])
  audios.append(sample["input_values"])
  gender.append(sample["gender"])
  accent.append(sample["accent"])
  tone.append(sample["tone"])

In [ ]:
import IPython.display as ipd

dashed = "_-_-"*100

for id_sample in range(len(predicted)):
  # Display the predicted text generated by the model
  print("Prediction:")
  print(processor.decode(predicted[id_sample]))

  # Display the reference (real) text
  print("\nReference:")
  print(real_sentences[id_sample])

  # Display the audio
  print("\nAudio:")
  speech = audios[id_sample]

  # Display the audio using IPython Audio with autoplay enabled
  ipd.display(ipd.Audio(data=speech, rate=16000))

  print(f'gender: {gender[id_sample]}, accent: {accent[id_sample]}, tone: {tone[id_sample]}')
  print(dashed)

Prediction:
چرا امروز آسمان انقدر عابی است

Reference:
چرا امروز آسمان انقدر آبی است؟ 

Audio:


gender: male, accent: فارسی, tone: incomplete
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
تشویش بستیار کالبد ما را می خشکند

Reference:
تشویش بسیار کالبد ما را میخشکاند 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
بیشتر مردن ب خاتر داشتن مذ نامتلوب از خردن آن خودداری میکنند

Reference:
 بیشتر مردم به خاطر داشتن مزه نامطلوب از خوردن ان خودداری میکنند. 

Audio:


gender: male , accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
تجربه بهترین معلم است

Reference:
تجربه بهترین معلم است. 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
از زیم ترین مجم استافتمانی و شاهکار معماری جهان باستان کدام است.

Reference:
عظیم ترین مجموعه ساختمانی و شاهکار معماری جهان باستان کدام است؟ 

Audio:


...

gender: male , accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
خرشید منبه استننو و گرما برای دمین اس

Reference:
خورشید منبع اصلی نور و گرما برای زمین است. 

Audio:


gender: male , accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
بهعوان نمونه و یک ایجا درنگیزه من بیام دو تا نمونه ب شمانشن بردم

Reference:
 به عنوان نمونه و یه ایجاد انگیزه من بیام دو تا نمونه به شما نشون بدم 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
سپس خود را پنهان کرد و تماشها کرد که آیا کسی تقت سنگ را از سرراه خودبر می دارد یا خیر

Reference:
 سپس خود را پنهان کرد و تماشا کرد که آیا کسی تخته سنگ را از سر راه خود برمی دارد یا خیر. 

Audio:


gender: male, accent: فارسی, tone: Normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
بسبارش به خدا و راحت بخواب.

Reference:
بسپارش به خدا و راحت بخواب . 

Audio:


gender: female, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
